In [ ]:
# !pip install emot
# !pip install symspellpy
# !pip install setuptools wheel
# !pip install spacy
# !pip install pyspellchecker
# !pip install spellchecker
# !pip install inflect
# !pip install langdetect
# !pip install google_trans_new
# !pip install deep-translator
# !pip install ekphrasis
# !pip install cdifflib
# !pip install gensim
# !pip install wordninja

In [1]:
import nltk
from nltk.corpus import PlaintextCorpusReader
import re, string, json

from symspellpy.symspellpy import SymSpell, Verbosity
import pkg_resources
import spacy
from tqdm.notebook import tqdm
from spellchecker import SpellChecker
import inflect

import difflib
import gensim

import pandas as pd

In [2]:
df = pd.read_csv("../../data/usa_combined.csv")
df

Text
0       want find way end racism try force people inje...
1       this child almost died tetanus, spent months h...
2       juste se rappeler m. leblanc la pression que l...
3       you would expect cases rise significantly, cou...
4       depends whether vaccination status is embedded...
...                                                   ...
423590           do it others.... 💪🎉💉🤙 #vaccinesaveslives
423591  got my first pfizer shot today. feeling well g...
423592  #fauciouchie #2 #vaccinated #vaccinesaveslives...
423593  yay 🙌🏻 congrats dr. j being fully vaccinated i...
423594  we all have do our part end this pandemic— get...

[423595 rows x 1 columns]

In [3]:
df.drop_duplicates(keep='first', inplace=True)

In [4]:
df

Text
0       want find way end racism try force people inje...
1       this child almost died tetanus, spent months h...
2       juste se rappeler m. leblanc la pression que l...
3       you would expect cases rise significantly, cou...
4       depends whether vaccination status is embedded...
...                                                   ...
423588  if you are eligible, please pre- register covi...
423590           do it others.... 💪🎉💉🤙 #vaccinesaveslives
423592  #fauciouchie #2 #vaccinated #vaccinesaveslives...
423593  yay 🙌🏻 congrats dr. j being fully vaccinated i...
423594  we all have do our part end this pandemic— get...

[404337 rows x 1 columns]

## Used hashtags

In [5]:
text = df['Text']
hashtag_list = []
for tweet in text:
#     print(tweet)
    hashtags = re.findall("#[A-Za-z0-9_]+", tweet)
    if len(hashtags) > 0:
        for tag in hashtags:
            hashtag_list.append(tag)

In [6]:
hashtag_list

['#covidvaccineconfidence',
 '#vanguardvaccinationproject',
 '#populationcontrol',
 '#omicron',
 '#vaccination',
 '#mentalhealth',
 '#psychtwitter',
 '#cdnpoli',
 '#onpoli',
 '#covid19',
 '#l',
 '#polqc',
 '#getvaccinated',
 '#vaccineswork',
 '#canada',
 '#superbowlmusicfest',
 '#socal',
 '#superbowlexperience',
 '#sblvi',
 '#hiringphenomenaltalent',
 '#security',
 '#covid19vaccine',
 '#vhcon',
 '#covid19vaccine',
 '#vhcon',
 '#covid19vaccine',
 '#vhcon',
 '#legaultmustresign',
 '#legault',
 '#covid19',
 '#localnews',
 '#newsbreak',
 '#covid',
 '#defundcbc',
 '#defundbbc',
 '#nyc',
 '#godblessamerica',
 '#nonads',
 '#votehelenkicknadlerny10',
 '#dyk',
 '#fightflu',
 '#heartmonth',
 '#nowplaying',
 '#nowspinning',
 '#np',
 '#nowstreaming',
 '#subgenius',
 '#joerogan',
 '#antivaxxers',
 '#covidab',
 '#covid19',
 '#repnotrip',
 '#ableg',
 '#ciuss_mcq',
 '#covid19',
 '#ambulance',
 '#inacceptable',
 '#k',
 '#jdq',
 '#covid19',
 '#mybodymychoice',
 '#rosiebartonappreciationday',
 '#ohio',
 

## Emoji Processing

In [7]:
import pickle
from emot.emo_unicode import UNICODE_EMOJI, EMOTICONS_EMO

In [8]:
# # 'Emoji_Dict.p'- download link https://drive.google.com/open?id=1G1vIkkbqPBYPKHcQ8qy0G2zkoab2Qv4v
with open('./Emoji_Dict.p', 'rb') as fp:
    Emoji_Dict = pickle.load(fp)
Emoji_Dict = {v: k for k, v in Emoji_Dict.items()}

# # Function for converting emojis into word
def convert_emojis(text):
    for emot in UNICODE_EMOJI:
        text = text.replace(emot, "_".join(UNICODE_EMOJI[emot].replace(",","").replace(":","").split()))
    return text

In [9]:
# TEST: line of text before emoji processing
df["Text"][107]

'amoa resort has activated its covid-19 protocols will welcome guests as it strictly observes social distancing, face masks wearing enforce vaccination cards-only entry.'

In [10]:
# TEST: convert_emoji function
convert_emojis(df['Text'][107])

'amoa resort has activated its covid-19 protocols will welcome guests as it strictly observes social distancing, face masks wearing enforce vaccination cards-only entry.'

In [ ]:
# emoji processing on df["text"] column

df["Text"] = df["Text"].astype(str)
df["new_text"] = df["Text"].apply(convert_emojis)

In [ ]:
df["new_text"][107]

## Emoticon Processing

In [11]:
# 'Emoticon_Dict.p'- download link https://drive.google.com/open?id=1HDpafp97gCl9xZTQWMgP2kKK_NuhENlE
with open('./Emoticon_Dict.p', 'rb') as fp:
    Emoticon_Dict = pickle.load(fp)
    
# Function for converting emoticons into word
def convert_emoticons(text):
    for emot in EMOTICONS_EMO:
        text = text.replace(emot, "_".join(EMOTICONS_EMO[emot].replace(",","").replace(":","").split()))
    return text

In [47]:
# TEST: convert_emoticons function
sentence_listtext = "Hello :-) :-)"
convert_emoticons(sentence_listtext)

'Hello Happy_face_smiley Happy_face_smiley'

In [12]:
df["new_text"] = df["new_text"].apply(convert_emoticons)

In [13]:
df.head()

Text  \
0  want find way end racism try force people inje...   
1  this child almost died tetanus, spent months h...   
2  juste se rappeler m. leblanc la pression que l...   
3  you would expect cases rise significantly, cou...   
4  depends whether vaccination status is embedded...   

                                            new_text  
0  want find way end racism try force people inje...  
1  this child almost died tetanus, spent months h...  
2  juste se rappeler m. leblanc la pression que l...  
3  you would expect cases rise significantly, cou...  
4  depends whether vaccination status is embedded...

In [14]:
# to deal with utf-8 that pycld can't handle
import regex

RE_BAD_CHARS = regex.compile(r"\p{Cc}|\p{Cs}")

def remove_bad_chars(text):
    return RE_BAD_CHARS.sub("", text)

remove_bad_chars("A\x96 bad char")  # Cc category
# 'A bad char'

'A bad char'

In [15]:
df['new_text'] = df['new_text'].apply(remove_bad_chars)

## Detecting Languages

In [16]:
import pycld2 as cld2

tweets = df['new_text']
language = []

for each in tweets:
    text_content = each
    _, _, _, detected_language = cld2.detect(text_content, returnVectors=True)
    language.append(detected_language)

In [17]:
langs = []

for each in language:
    lang_detected = ""
    for i in range(0,len(each)):
        lang_extracted = each[i][2]
        if i != (len(each) - 1):
            lang_detected += lang_extracted + ", "
        else:
            lang_detected += lang_extracted
    langs.append(lang_detected)

In [18]:
langs

['ENGLISH',
 'ENGLISH',
 'FRENCH',
 'ENGLISH',
 'ENGLISH',
 'ENGLISH',
 'ENGLISH',
 'ENGLISH',
 'ENGLISH',
 'ENGLISH',
 'ENGLISH',
 'ENGLISH',
 'ENGLISH',
 'Unknown',
 'ENGLISH',
 'FRENCH',
 'ENGLISH',
 'ENGLISH',
 'ENGLISH',
 'ENGLISH',
 'ENGLISH',
 'ENGLISH',
 'ENGLISH',
 'ENGLISH',
 'ENGLISH',
 'ENGLISH',
 'ENGLISH',
 'ENGLISH',
 'ENGLISH',
 'ENGLISH',
 'ENGLISH',
 'ENGLISH',
 'ENGLISH',
 'ENGLISH',
 'ENGLISH',
 'FRENCH',
 'ENGLISH',
 'ENGLISH',
 'FRENCH',
 'ENGLISH',
 'ENGLISH',
 'ENGLISH',
 'ENGLISH',
 'ENGLISH',
 'FRENCH',
 'ENGLISH',
 'ENGLISH',
 'ENGLISH',
 'FRENCH',
 'ENGLISH',
 'ENGLISH',
 'ENGLISH',
 'ENGLISH',
 'ENGLISH',
 'Unknown',
 'ENGLISH',
 'ENGLISH',
 'ENGLISH',
 'ENGLISH',
 'ENGLISH',
 'ENGLISH',
 'ENGLISH',
 'ENGLISH',
 'Unknown',
 'FRENCH',
 'ENGLISH',
 'FRENCH',
 'ENGLISH',
 'ENGLISH',
 'ENGLISH',
 'ENGLISH',
 'ENGLISH',
 'ENGLISH',
 'ENGLISH',
 'ENGLISH',
 'ENGLISH',
 'ENGLISH',
 'ENGLISH',
 'ENGLISH',
 'ENGLISH',
 'ENGLISH',
 'ENGLISH',
 'ENGLISH',
 'ENGLISH',


In [19]:
df['languages'] = langs
df

Text  \
0       want find way end racism try force people inje...   
1       this child almost died tetanus, spent months h...   
2       juste se rappeler m. leblanc la pression que l...   
3       you would expect cases rise significantly, cou...   
4       depends whether vaccination status is embedded...   
...                                                   ...   
423588  if you are eligible, please pre- register covi...   
423590           do it others.... 💪🎉💉🤙 #vaccinesaveslives   
423592  #fauciouchie #2 #vaccinated #vaccinesaveslives...   
423593  yay 🙌🏻 congrats dr. j being fully vaccinated i...   
423594  we all have do our part end this pandemic— get...   

                                                 new_text languages  
0       want find way end racism try force people inje...   ENGLISH  
1       this child almost died tetanus, spent months h...   ENGLISH  
2       juste se rappeler m. leblanc la pression que l...    FRENCH  
3       you would expect cases rise significantly, cou...   ENGLISH  
4       depends whether vaccination status is embedded...   ENGLISH  
...                                                   ...       ...  
423588  if you are eligible, please pre- register covi...   ENGLISH  
423590  do it others.... flexed_bicepsparty_poppersyri...   ENGLISH  
423592  #fauciouchie #2 #vaccinated #vaccinesaveslives...   Unknown  
423593  yay raising_handslight_skin_tone congrats dr. ...   ENGLISH  
423594  we all have do our part end this pandemic— get...   ENGLISH  

[404337 rows x 3 columns]

In [20]:
df[df['languages'] != 'ENGLISH'].head()
#check how many rows

Text  \
2   juste se rappeler m. leblanc la pression que l...   
13                                        vaccination   
15  1-je comprends exactement ce qui doit être com...   
35  environ 500 médecins spécialistes participaien...   
38  c'est bien dommage que ce soit un droit, leur ...   

                                             new_text languages  
2   juste se rappeler m. leblanc la pression que l...    FRENCH  
13                                        vaccination   Unknown  
15  1-je comprends exactement ce qui doit être com...    FRENCH  
35  environ 500 médecins spécialistes participaien...    FRENCH  
38  c'est bien dommage que ce soit un droit, leur ...    FRENCH

In [21]:
df[df['languages'] != 'ENGLISH']['new_text']

2         juste se rappeler m. leblanc la pression que l...
13                                              vaccination
15        1-je comprends exactement ce qui doit être com...
35        environ 500 médecins spécialistes participaien...
38        c'est bien dommage que ce soit un droit, leur ...
                                ...                        
423579                             ayep. #vaccinesaveslives
423582    continue wear your mask preferably double , ge...
423585        #vaccinated #vaccinesaveslives syringemicrobe
423586    #vaccine #maskup #vaccinesaveslives #vaccinesi...
423592    #fauciouchie #2 #vaccinated #vaccinesaveslives...
Name: new_text, Length: 56002, dtype: object

In [91]:
df[df['languages'] != 'ENGLISH']['new_text'][105977]

'it’s time you do your part this fight against covid we reward you your actions we are sure we together be victorious this fight with collective effort everyone raising_handsmedium_skin_tone #vaccinesaveslives #weareinthistogether #plasmadonation #spreadpositivity'

In [22]:
df.to_csv('usa_after_language_detection.csv')

## Language Translation

In [1]:
# df = pd.read_csv('../data/usa_after_language_detection.csv')

In [ ]:
from deep_translator import GoogleTranslator

non_english = df[df['languages'] != 'ENGLISH']['new_text']

translated = []

for each in non_english:
    translate = GoogleTranslator(source='auto', target='en').translate(each)
    translated.append(translate)

In [ ]:
translated

In [ ]:
#creating new_text column
df['new_text'] = df['Text']

In [ ]:
non_english = df[df['languages'] != 'ENGLISH']

In [ ]:
non_english.head()
#33981 rows

In [ ]:
indexes_list = non_english.index

In [ ]:
indexes_list

In [ ]:
len(indexes_list)

In [ ]:
# range_firstNum = start_range + start_batch

# new_indexes_list = []

# for num in indexes_list:
#     new = num - range_firstNum
#     new_indexes_list.append(new)

In [ ]:
for i in range(0,len(indexes_list)):
    index = indexes_list[i]
    df.iloc[index]['new_text'] = translated[i]

In [ ]:
#check that the new_text col to see to check that the initial non-english rows have been translated
df[df['languages'] != 'ENGLISH']

## Language Detection Part 2

In [ ]:
# import pycld2 as cld2

# reviews = df['new_text_after_translation']
# language2 = []

# for each in reviews:
#     text_content = each
#     _, _, _, detected_language = cld2.detect(text_content, returnVectors=True)
#     language2.append(detected_language)

In [ ]:
# langs2 = []

# for each in language2:
#     lang_detected = ""
#     for i in range(0,len(each)):
#         lang_extracted = each[i][2]
#         if i != (len(each) - 1):
#             lang_detected += lang_extracted + ", "
#         else:
#             lang_detected += lang_extracted
#     langs2.append(lang_detected)

In [ ]:
# langs2

In [ ]:
# df['new_languages'] = langs2

In [ ]:
# df.to_csv("usa-after-langdetectandtrans.csv")

In [ ]:
# non_english2 = df[df['new_languages'] != 'ENGLISH']
# non_english2

In [ ]:
#see how many still detected as non-english, brieflcheck is it rly non english
# non_english2.info()

In [ ]:
# non_english2.to_csv('non_english2.csv')

## Read df after translation (USA)

In [63]:
df = pd.read_csv('./df_after_translation_usa.csv')

In [64]:
df.head()

Unnamed: 0                                               Text  \
0           0  want find way end racism try force people inje...   
1           1  this child almost died tetanus, spent months h...   
2           2  juste se rappeler m. leblanc la pression que l...   
3           3  you would expect cases rise significantly, cou...   
4           4  depends whether vaccination status is embedded...   

                                            new_text languages  \
0  want find way end racism try force people inje...   ENGLISH   
1  this child almost died tetanus, spent months h...   ENGLISH   
2  juste se rappeler m. leblanc la pression que l...    FRENCH   
3  you would expect cases rise significantly, cou...   ENGLISH   
4  depends whether vaccination status is embedded...   ENGLISH   

                          new_text_after_translation  
0  want find way end racism try force people inje...  
1  this child almost died tetanus, spent months h...  
2  just remember mr. leblanc the pressure that th...  
3  you would expect cases rise significantly, cou...  
4  depends whether vaccination status is embedded...

In [65]:
df

Unnamed: 0                                               Text  \
0                0  want find way end racism try force people inje...   
1                1  this child almost died tetanus, spent months h...   
2                2  juste se rappeler m. leblanc la pression que l...   
3                3  you would expect cases rise significantly, cou...   
4                4  depends whether vaccination status is embedded...   
...            ...                                                ...   
404260      404260  if you are eligible, please pre- register covi...   
404261      404261           do it others.... 💪🎉💉🤙 #vaccinesaveslives   
404262      404262  #fauciouchie #2 #vaccinated #vaccinesaveslives...   
404263      404263  yay 🙌🏻 congrats dr. j being fully vaccinated i...   
404264      404264  we all have do our part end this pandemic— get...   

                                                 new_text languages  \
0       want find way end racism try force people inje...   ENGLISH   
1       this child almost died tetanus, spent months h...   ENGLISH   
2       juste se rappeler m. leblanc la pression que l...    FRENCH   
3       you would expect cases rise significantly, cou...   ENGLISH   
4       depends whether vaccination status is embedded...   ENGLISH   
...                                                   ...       ...   
404260  if you are eligible, please pre- register covi...   ENGLISH   
404261  do it others.... flexed_bicepsparty_poppersyri...   ENGLISH   
404262  #fauciouchie #2 #vaccinated #vaccinesaveslives...   ENGLISH   
404263  yay raising_handslight_skin_tone congrats dr. ...   ENGLISH   
404264  we all have do our part end this pandemic— get...   ENGLISH   

                               new_text_after_translation  
0       want find way end racism try force people inje...  
1       this child almost died tetanus, spent months h...  
2       just remember mr. leblanc the pressure that th...  
3       you would expect cases rise significantly, cou...  
4       depends whether vaccination status is embedded...  
...                                                   ...  
404260  if you are eligible, please pre- register covi...  
404261  do it others.... flexed_bicepsparty_poppersyri...  
404262  #fauciouchie #2 #vaccinated #vaccinesaveslives...  
404263  yay raising_handslight_skin_tone congrats dr. ...  
404264  we all have do our part end this pandemic— get...  

[404265 rows x 5 columns]

In [66]:
df.drop('Unnamed: 0', axis=1, inplace=True)

In [67]:
df

Text  \
0       want find way end racism try force people inje...   
1       this child almost died tetanus, spent months h...   
2       juste se rappeler m. leblanc la pression que l...   
3       you would expect cases rise significantly, cou...   
4       depends whether vaccination status is embedded...   
...                                                   ...   
404260  if you are eligible, please pre- register covi...   
404261           do it others.... 💪🎉💉🤙 #vaccinesaveslives   
404262  #fauciouchie #2 #vaccinated #vaccinesaveslives...   
404263  yay 🙌🏻 congrats dr. j being fully vaccinated i...   
404264  we all have do our part end this pandemic— get...   

                                                 new_text languages  \
0       want find way end racism try force people inje...   ENGLISH   
1       this child almost died tetanus, spent months h...   ENGLISH   
2       juste se rappeler m. leblanc la pression que l...    FRENCH   
3       you would expect cases rise significantly, cou...   ENGLISH   
4       depends whether vaccination status is embedded...   ENGLISH   
...                                                   ...       ...   
404260  if you are eligible, please pre- register covi...   ENGLISH   
404261  do it others.... flexed_bicepsparty_poppersyri...   ENGLISH   
404262  #fauciouchie #2 #vaccinated #vaccinesaveslives...   ENGLISH   
404263  yay raising_handslight_skin_tone congrats dr. ...   ENGLISH   
404264  we all have do our part end this pandemic— get...   ENGLISH   

                               new_text_after_translation  
0       want find way end racism try force people inje...  
1       this child almost died tetanus, spent months h...  
2       just remember mr. leblanc the pressure that th...  
3       you would expect cases rise significantly, cou...  
4       depends whether vaccination status is embedded...  
...                                                   ...  
404260  if you are eligible, please pre- register covi...  
404261  do it others.... flexed_bicepsparty_poppersyri...  
404262  #fauciouchie #2 #vaccinated #vaccinesaveslives...  
404263  yay raising_handslight_skin_tone congrats dr. ...  
404264  we all have do our part end this pandemic— get...  

[404265 rows x 4 columns]

## Text File & Corpus Creation

In [8]:
# create txt file for each text review

# def CreateCorpusFromDataFrame(corpusfolder, df):
#     for index, r in df.iterrows():
#     # print (r['text'])
#     # print (str(index) + '.txt')
#         text = r['new_text_after_translation']
#         fname = str(index)+'.txt'
#         corpusfile = open(corpusfolder+'/'+fname, "w", encoding="utf-8")
#         corpusfile.write(str(text))
#         corpusfile.close()

# CreateCorpusFromDataFrame('../text-corpus-usa-v2', df)

# reference: https://stackoverflow.com/questions/49088978/how-to-create-corpus-from-pandas-data-frame-to-operate-with-nltk/49104725

In [2]:
file_directory = '../../text-corpus-usa-v2'
filename_pattern = '.+\.txt'

my_corpus = PlaintextCorpusReader(file_directory, filename_pattern)

#Print some words in specific file
test = my_corpus.words('0.txt')
print(test)
print(len(test))

['want', 'find', 'way', 'end', 'racism', 'try', ...]
52


In [3]:
#Total number of text files i.e. total number of tweets
print(len(my_corpus.fileids()))

404265


In [4]:
fdist = nltk.FreqDist(test)
print(fdist.most_common(10))

[('people', 4), ('.', 4), ('i', 3), ('force', 2), ('against', 2), ('vaxx', 2), ('want', 1), ('find', 1), ('way', 1), ('end', 1)]


In [ ]:
# word distribution across all files
fdist_all_files = nltk.FreqDist(my_corpus.words())
print(fdist_all_files.most_common(10))

In [ ]:
#total number of words
total_words = my_corpus.words()
print(total_words)
print(len(total_words))

## Tokenization

In [5]:
#Creating a sorted list of texts since my_corpus.fileids() does not read texts consecutively
#EDIT RANGE
sorted_list = [f'{i}.txt' for i in range(0, 404265)]

In [6]:
tokenised_words = [my_corpus.words(each) for each in sorted_list]
tokenised_words

[['want', 'find', 'way', 'end', 'racism', 'try', ...],
 ['this', 'child', 'almost', 'died', 'tetanus', ',', ...],
 ['just', 'remember', 'mr', '.', 'leblanc', 'the', ...],
 ['you', 'would', 'expect', 'cases', 'rise', ...],
 ['depends', 'whether', 'vaccination', 'status', 'is', ...],
 ['it', 'could', 'have', 'ripped', '…', 'harder', 'or', ...],
 ['they', 'do', 'this', 'at', 'vaccination', 'centres', ...],
 ['part', 'vanguard', 'vaccination', 'awareness', ...],
 ['correct', '.', 'it', '’', 's', 'not', 'about', ...],
 ['does', 'it', 'hurt', 'your', 'head', 'actually', ...],
 ['world', '-', 'wide', 'mass', 'vaccination', ...],
 ['as', 'vaccinations', '...', 'you', "'", 'll', ...],
 ['following', 'tweet', 'didn', "'", 't', 'even', 'age', ...],
 ['vaccination'],
 ['private', 'businesses', 'can', 'enforce', ...],
 ['1', '-', 'I', 'understand', 'exactly', 'what', ...],
 ['story', 'with', 'martha', 'mccallum', ',', 'am', ...],
 ['world', "'", 's', 'top', 'virologist', ',', 'luc', ...],
 ['obviou

In [7]:
print(len(tokenised_words))

404265


## Converting British to American English

In [8]:
#https://stackoverflow.com/questions/42329766/python-nlp-british-english-vs-american-english

import requests

def americanize(word):
    url ="https://raw.githubusercontent.com/hyperreality/American-British-English-Translator/master/data/british_spellings.json"
    british_to_american_dict = requests.get(url).json()

    for british_spelling, american_spelling in british_to_american_dict.items():
        word = word.replace(british_spelling, american_spelling)
  
    return word

In [9]:
test_americanize = [['flavour', 'colour'], ['apologise', 'travelled']]
test_americanize = [[americanize(w) for w in each] for each in test_americanize]
test_americanize

[['flavor', 'color'], ['apologize', 'traveled']]

In [10]:
tokenised = [[americanize(w) for w in each] for each in tokenised_words[137000:142000]]
tokenised

[['damn',
  'modern',
  'left',
  'I',
  'thought',
  'it',
  'represented',
  'a',
  'small',
  'bread',
  '.',
  'Rather',
  ',',
  'the',
  'extreme',
  'right',
  ',',
  'as',
  'demonstrated',
  'by',
  'the',
  'governments',
  'of',
  'Jalisco',
  'and',
  'NL',
  '.'],
 ['thar',
  'happened',
  'because',
  'they',
  'locked',
  'down',
  ',',
  'numbers',
  'down',
  'then',
  'reopened',
  'numbers',
  'up',
  '.',
  'it',
  'is',
  'same',
  'wave',
  'prolonged',
  '.',
  'why',
  'lockdowns',
  'at',
  'this',
  'point',
  'don',
  "'",
  't',
  'work',
  '.',
  'that',
  'person',
  'u',
  'disagree',
  'with',
  'helped',
  'develop',
  'moderna',
  'vax',
  '&',
  'amp',
  ';',
  'working',
  'omicron',
  'booster',
  '.'],
 ['Can',
  'I',
  'remove',
  '2',
  'doses',
  'of',
  'moderna',
  'from',
  'the',
  'body',
  'this',
  'way',
  '?'],
 ['On',
  'the',
  'other',
  'hand',
  ',',
  'Marina',
  'also',
  'vaccinated',
  'the',
  'lazy',
  'masters',
  'who',
  '

In [11]:
# save americanized tokens
convert_to_str = []

for each in tokenised:
    converted_str = ""
    for i in range(0,len(each)):
        if i == (len(each) - 1):
            converted_str += each[i]
        else:
            converted_str += each[i] + ", "
    convert_to_str.append(converted_str)
    
converted_df = pd.DataFrame(convert_to_str)

converted_df.to_csv('usa_americanized_tokens_137000-142000.csv')

## Conversion to numerals

In [12]:
#check if text has numbers 
def hasNumbers(inputList):
    for list in inputList:
        for word in list:
            if word.isdigit():
                return True
    return False

hasNumbers(tokenised)

True

In [13]:
# since theres numbers, the numbers need to be converted to words e.g. "2" to "two"

p = inflect.engine()
  
# convert number into words
def convert_number(text):
    # split string into list of words
    temp_str = text.split()
    # initialise empty list
    new_string = []
  
    for word in temp_str:
        # if word is a digit, convert the digit
        # to numbers and append into the new_string list
        if word.isdigit():
            temp = p.number_to_words(word)
            new_string.append(temp)
  
        # append the word as it is
        else:
            new_string.append(word)
  
    # join the words of new_string to form a string
    temp_str = ' '.join(new_string)
    return temp_str

In [14]:
# example text which contain numbers in it
input_list = ['There are 3 balls in this bag, and 12 in the other one.', '29']
result = [convert_number(each)for each in input_list]
result

['There are three balls in this bag, and twelve in the other one.',
 'twenty-nine']

In [15]:
#NEED TO CHANGE VARIABLE after us to brit eng conversion

tokenised_numerals_converted = [[convert_number(w) for w in each] for each in tokenised]

In [16]:
#check if text has numbers 
def hasNumbers(inputList):
    for list in inputList:
        for word in list:
            if word.isdigit():
                return True
    return False

hasNumbers(tokenised_numerals_converted)

False

## Misspellings

In [17]:
def correct_typo(tokens):
    spell = SpellChecker()
    return [spell.correction(t) if len(spell.unknown([t]))>0 else t for t in tokens]

In [18]:
misspelled_test = ['greot', 'coyor', 'and', 'misspeling']
correct_typo(misspelled_test)

['great', 'color', 'and', 'misspelling']

In [19]:
tokenised_spellchecked = [correct_typo(each) for each in tokenised_numerals_converted]

In [20]:
tokenised_spellchecked

[['damn',
  'modern',
  'left',
  'I',
  'thought',
  'it',
  'represented',
  'a',
  'small',
  'bread',
  '.',
  'Rather',
  ',',
  'the',
  'extreme',
  'right',
  ',',
  'as',
  'demonstrated',
  'by',
  'the',
  'governments',
  'of',
  'calico',
  'and',
  'no',
  '.'],
 ['thar',
  'happened',
  'because',
  'they',
  'locked',
  'down',
  ',',
  'numbers',
  'down',
  'then',
  'reopened',
  'numbers',
  'up',
  '.',
  'it',
  'is',
  'same',
  'wave',
  'prolonged',
  '.',
  'why',
  'lockdowns',
  'at',
  'this',
  'point',
  'don',
  "'",
  'i',
  'work',
  '.',
  'that',
  'person',
  'u',
  'disagree',
  'with',
  'helped',
  'develop',
  'modern',
  'van',
  '&',
  'amp',
  ';',
  'working',
  'omicron',
  'booster',
  '.'],
 ['Can',
  'I',
  'remove',
  'two',
  'doses',
  'of',
  'modern',
  'from',
  'the',
  'body',
  'this',
  'way',
  '?'],
 ['On',
  'the',
  'other',
  'hand',
  ',',
  'Marina',
  'also',
  'vaccinated',
  'the',
  'lazy',
  'masters',
  'who',
  'o

In [21]:
convert_to_str = []

for each in tokenised_spellchecked:
    converted_str = ""
    for i in range(0,len(each)):
        if i == (len(each) - 1):
            converted_str += each[i]
        else:
            converted_str += each[i] + ", "
    convert_to_str.append(converted_str)
    
converted_df = pd.DataFrame(convert_to_str)

converted_df.to_csv('corrected-137000-142000.csv')

In [22]:
converted_df

0
0     damn, modern, left, I, thought, it, represente...
1     thar, happened, because, they, locked, down, ,...
2     Can, I, remove, two, doses, of, modern, from, ...
3     On, the, other, hand, ,, Marina, also, vaccina...
4     we, have, plenty, #, modern, #, covid19, #, va...
...                                                 ...
4995  busy, day, at, work, ., got, blood, drawn, bot...
4996  now, i, ', i, boosted, ,, just, like, my, wax,...
4997  i, nine, out, ten, modern, doses, have, gone, ...
4998  my, arm, my, modern, booster, shot, isn, i, i,...
4999  remember, what, happened, modern, when, you, s...

[5000 rows x 1 columns]

## Compiled CSV

In [ ]:
df2 = pd.read_csv("compiled-after-correction.csv")

In [ ]:
new_tokenised_spellchecked = []

for row in df2['0']:
    alist = row.split(", ")
    new_tokenised_spellchecked.append(alist)

In [ ]:
new_tokenised_spellchecked

## Convert to lowercase

In [23]:
#NEED TO CHANGE VARIABLE AFTER SPELLCHECK

tokenised_lower = [[w.lower() for w in each] for each in tokenised_spellchecked]
tokenised_lower

[['pfizer',
  'shot',
  'one',
  'finally',
  'syringe',
  'so',
  'very',
  'grateful',
  'folded_handslight_skin_tone',
  '#',
  'covidvaccination',
  '#',
  'pfizer',
  '#',
  'thankyouscience'],
 ['my',
  'sweet',
  'boy',
  'gabriel',
  'got',
  'his',
  'first',
  'dose',
  '#',
  'pfizer',
  'today',
  '.',
  'he',
  "'",
  'i',
  'such',
  'champ',
  '...',
  'flexed_bicepssyringebeating_heartleo'],
 ['est',
  'dose',
  '#',
  'pfizer',
  'vaccine',
  'syringethumbs_uplight_skin_tonethumbs_uplight_skin_tonethumbs_uplight_skin_tonesign_of_the_hornslight_skin_tonesign_of_the_hornslight_skin_tonesign_of_the_hornslight_skin_tone',
  '@',
  'bucks',
  'county',
  'community',
  'college',
  'i',
  'lower',
  'bucks',
  'campus'],
 ['i',
  'just',
  'got',
  'my',
  'est',
  'coronavirus',
  'couid',
  '-',
  'nineteen',
  'pfizer',
  'shot',
  '@',
  'franciscan',
  'health',
  'hammond',
  '-',
  'hammond',
  ','],
 ['i', 'i', 'i', 'pfizer', 'girl', 'yep'],
 ['i',
  "'",
  'i',
  '

## Remove punctuation

In [24]:
# remove punctuations from tokenised_lower
tokenised_words_only = [[w for w in each if re.search('^[a-z]+$',w)] for each in tokenised_lower]
tokenised_words_only

[['pfizer',
  'shot',
  'one',
  'finally',
  'syringe',
  'so',
  'very',
  'grateful',
  'covidvaccination',
  'pfizer',
  'thankyouscience'],
 ['my',
  'sweet',
  'boy',
  'gabriel',
  'got',
  'his',
  'first',
  'dose',
  'pfizer',
  'today',
  'he',
  'i',
  'such',
  'champ'],
 ['est',
  'dose',
  'pfizer',
  'vaccine',
  'bucks',
  'county',
  'community',
  'college',
  'i',
  'lower',
  'bucks',
  'campus'],
 ['i',
  'just',
  'got',
  'my',
  'est',
  'coronavirus',
  'couid',
  'nineteen',
  'pfizer',
  'shot',
  'franciscan',
  'health',
  'hammond',
  'hammond'],
 ['i', 'i', 'i', 'pfizer', 'girl', 'yep'],
 ['i',
  'i',
  'wondering',
  'if',
  'it',
  'i',
  'worth',
  'getting',
  'i',
  'amp',
  'i',
  'even',
  'though',
  'i',
  've',
  'already',
  'got',
  'two',
  'pfizer',
  'shots',
  'i',
  'figure',
  'double',
  'protection',
  'plus',
  'free',
  'hot',
  'dog'],
 ['second',
  'dose',
  'pfizer',
  'accomplished',
  'now',
  'rest',
  'bit',
  'before',
  'fi

## Remove words len <= 3

In [52]:
# new_list = []

# for alist in tokenised_words_only:
#     mini_list = []
#     for word in alist:
#         if len(word) > 3:
#             mini_list.append(word)
#     new_list.append(mini_list)

In [53]:
# #test
# new_list

[['want',
  'find',
  'racism',
  'force',
  'people',
  'inject',
  'themselves',
  'that',
  'what',
  'bunch',
  'people',
  'races',
  'standing',
  'against',
  'forced',
  'vaccination',
  'against',
  'vaxx',
  'some',
  'people',
  'need',
  'these',
  'vaxx',
  'support',
  'those',
  'people',
  'getting',
  'their',
  'shot',
  'draw',
  'line',
  'force'],
 ['this',
  'child',
  'almost',
  'died',
  'tetanus',
  'spent',
  'months',
  'hospital',
  'cost',
  'around',
  'parents',
  'still',
  'refused',
  'vaccination',
  'after',
  'this',
  'pandemic'],
 ['just',
  'remember',
  'leblanc',
  'pressure',
  'that',
  'provincial',
  'business',
  'world',
  'asked',
  'able',
  'open',
  'borders',
  'traffic',
  'will',
  'provincial',
  'govt',
  'included',
  'block',
  'tourists',
  'will',
  'have',
  'pass',
  'vaccination',
  'hotel',
  'restaurant'],
 ['would',
  'expect',
  'cases',
  'rise',
  'significantly',
  'course',
  'vaccination',
  'rates',
  'come',
  

In [54]:
# tokenised_words_only = new_list

In [55]:
# tokenised_words_only

[['want',
  'find',
  'racism',
  'force',
  'people',
  'inject',
  'themselves',
  'that',
  'what',
  'bunch',
  'people',
  'races',
  'standing',
  'against',
  'forced',
  'vaccination',
  'against',
  'vaxx',
  'some',
  'people',
  'need',
  'these',
  'vaxx',
  'support',
  'those',
  'people',
  'getting',
  'their',
  'shot',
  'draw',
  'line',
  'force'],
 ['this',
  'child',
  'almost',
  'died',
  'tetanus',
  'spent',
  'months',
  'hospital',
  'cost',
  'around',
  'parents',
  'still',
  'refused',
  'vaccination',
  'after',
  'this',
  'pandemic'],
 ['just',
  'remember',
  'leblanc',
  'pressure',
  'that',
  'provincial',
  'business',
  'world',
  'asked',
  'able',
  'open',
  'borders',
  'traffic',
  'will',
  'provincial',
  'govt',
  'included',
  'block',
  'tourists',
  'will',
  'have',
  'pass',
  'vaccination',
  'hotel',
  'restaurant'],
 ['would',
  'expect',
  'cases',
  'rise',
  'significantly',
  'course',
  'vaccination',
  'rates',
  'come',
  

## POS Tagging

In [25]:
tokens = tokenised_words_only[0]
tokens

['pfizer',
 'shot',
 'one',
 'finally',
 'syringe',
 'so',
 'very',
 'grateful',
 'covidvaccination',
 'pfizer',
 'thankyouscience']

In [26]:
nltk.pos_tag(tokens)

[('pfizer', 'NN'),
 ('shot', 'NN'),
 ('one', 'CD'),
 ('finally', 'RB'),
 ('syringe', 'VBP'),
 ('so', 'RB'),
 ('very', 'RB'),
 ('grateful', 'JJ'),
 ('covidvaccination', 'NN'),
 ('pfizer', 'NN'),
 ('thankyouscience', 'NN')]

In [27]:
pos_tagged = []

for each in tokenised_words_only:
    pos_tags = nltk.pos_tag(each)
    pos_tagged.append(pos_tags)

In [28]:
pos_tagged

[[('pfizer', 'NN'),
  ('shot', 'NN'),
  ('one', 'CD'),
  ('finally', 'RB'),
  ('syringe', 'VBP'),
  ('so', 'RB'),
  ('very', 'RB'),
  ('grateful', 'JJ'),
  ('covidvaccination', 'NN'),
  ('pfizer', 'NN'),
  ('thankyouscience', 'NN')],
 [('my', 'PRP$'),
  ('sweet', 'JJ'),
  ('boy', 'JJ'),
  ('gabriel', 'NN'),
  ('got', 'VBD'),
  ('his', 'PRP$'),
  ('first', 'JJ'),
  ('dose', 'JJ'),
  ('pfizer', 'NN'),
  ('today', 'NN'),
  ('he', 'PRP'),
  ('i', 'VBZ'),
  ('such', 'JJ'),
  ('champ', 'NNS')],
 [('est', 'JJS'),
  ('dose', 'JJ'),
  ('pfizer', 'NN'),
  ('vaccine', 'NN'),
  ('bucks', 'NNS'),
  ('county', 'VBP'),
  ('community', 'NN'),
  ('college', 'NN'),
  ('i', 'NN'),
  ('lower', 'RBR'),
  ('bucks', 'NNS'),
  ('campus', 'VBP')],
 [('i', 'NN'),
  ('just', 'RB'),
  ('got', 'VBD'),
  ('my', 'PRP$'),
  ('est', 'JJS'),
  ('coronavirus', 'NN'),
  ('couid', 'NN'),
  ('nineteen', 'JJ'),
  ('pfizer', 'NN'),
  ('shot', 'JJ'),
  ('franciscan', 'JJ'),
  ('health', 'NN'),
  ('hammond', 'NN'),
  ('hammond

In [29]:
df = pd.read_csv("corrected-97000-102000.csv")
df.drop(['Unnamed: 0'], axis=1, inplace=True)
df.rename(columns={'0': 'Text'}, inplace = True)

In [30]:
df['pos_tagged_words'] = pos_tagged

In [31]:
df.head()

Text  \
0  pfizer, shot, one, finally, syringe, so, very,...   
1  my, sweet, boy, gabriel, got, his, first, dose...   
2  est, dose, #, pfizer, vaccine, syringethumbs_u...   
3  i, just, got, my, est, coronavirus, couid, -, ...   
4                         i, i, i, pfizer, girl, yep   

                                    pos_tagged_words  
0  [(pfizer, NN), (shot, NN), (one, CD), (finally...  
1  [(my, PRP$), (sweet, JJ), (boy, JJ), (gabriel,...  
2  [(est, JJS), (dose, JJ), (pfizer, NN), (vaccin...  
3  [(i, NN), (just, RB), (got, VBD), (my, PRP$), ...  
4  [(i, NN), (i, VBP), (i, VBP), (pfizer, VBP), (...

## Stop word removal

In [32]:
# TEST: remove stop words from test_words_only
from nltk.corpus import stopwords
stop_list = stopwords.words('english')

test_words_only1 = ['not', 'great', 'color', 'and', 'cruelty', 'free', 'i', 'use', 'elf', 'cosmetics', 'every', 'day', 'and', 'i', 'love', 'it']
test_stopremoved = [w for w in test_words_only1 if w not in stop_list or w == 'not']
print(test_stopremoved)

['not', 'great', 'color', 'cruelty', 'free', 'use', 'elf', 'cosmetics', 'every', 'day', 'love']


In [33]:
# remove stop words from tokenised_words_only
from nltk.corpus import stopwords
stop_list = stopwords.words('english')
tokenised_stopremoved = [[w for w in each if w not in stop_list or w == 'not'] for each in tokenised_words_only]
tokenised_stopremoved

[['pfizer',
  'shot',
  'one',
  'finally',
  'syringe',
  'grateful',
  'covidvaccination',
  'pfizer',
  'thankyouscience'],
 ['sweet',
  'boy',
  'gabriel',
  'got',
  'first',
  'dose',
  'pfizer',
  'today',
  'champ'],
 ['est',
  'dose',
  'pfizer',
  'vaccine',
  'bucks',
  'county',
  'community',
  'college',
  'lower',
  'bucks',
  'campus'],
 ['got',
  'est',
  'coronavirus',
  'couid',
  'nineteen',
  'pfizer',
  'shot',
  'franciscan',
  'health',
  'hammond',
  'hammond'],
 ['pfizer', 'girl', 'yep'],
 ['wondering',
  'worth',
  'getting',
  'amp',
  'even',
  'though',
  'already',
  'got',
  'two',
  'pfizer',
  'shots',
  'figure',
  'double',
  'protection',
  'plus',
  'free',
  'hot',
  'dog'],
 ['second',
  'dose',
  'pfizer',
  'accomplished',
  'rest',
  'bit',
  'finishing',
  'packing',
  'cleaning',
  'donation',
  'runs'],
 ['anderson', 'got', 'tickets', 'pfizer'],
 ['think',
  'uk',
  'study',
  'looking',
  'mixing',
  'vaccines',
  'bodes',
  'well',
  'far

## Bigram & Trigram Models

In [34]:
# Build the bigram and trigram models
bigram = gensim.models.Phrases(tokenised_stopremoved, min_count=5, threshold=100) # higher threshold fewer phrases.
trigram = gensim.models.Phrases(bigram[tokenised_stopremoved], threshold=100)
# Faster way to get a sentence clubbed as a trigram/bigram
bigram_mod = gensim.models.phrases.Phraser(bigram)
trigram_mod = gensim.models.phrases.Phraser(trigram)

In [35]:
def make_bigrams(texts):
    return [bigram_mod[doc] for doc in texts]
def make_trigrams(texts):
    return [trigram_mod[bigram_mod[doc]] for doc in texts]

In [36]:
# Form Bigrams
tokenised_bigrams = make_bigrams(tokenised_stopremoved)
# Form Trigrams
tokenised_trigrams = make_trigrams(tokenised_stopremoved)

In [37]:
tokenised_bigrams

[['pfizer',
  'shot',
  'one',
  'finally',
  'syringe',
  'grateful',
  'covidvaccination',
  'pfizer',
  'thankyouscience'],
 ['sweet',
  'boy',
  'gabriel',
  'got',
  'first',
  'dose',
  'pfizer',
  'today',
  'champ'],
 ['est',
  'dose',
  'pfizer',
  'vaccine',
  'bucks',
  'county',
  'community',
  'college',
  'lower',
  'bucks',
  'campus'],
 ['got',
  'est',
  'coronavirus',
  'couid',
  'nineteen',
  'pfizer',
  'shot',
  'franciscan',
  'health',
  'hammond',
  'hammond'],
 ['pfizer', 'girl', 'yep'],
 ['wondering',
  'worth',
  'getting',
  'amp',
  'even',
  'though',
  'already',
  'got',
  'two',
  'pfizer',
  'shots',
  'figure',
  'double',
  'protection',
  'plus',
  'free',
  'hot',
  'dog'],
 ['second',
  'dose',
  'pfizer',
  'accomplished',
  'rest',
  'bit',
  'finishing',
  'packing',
  'cleaning',
  'donation',
  'runs'],
 ['anderson', 'got', 'tickets', 'pfizer'],
 ['think',
  'uk',
  'study',
  'looking',
  'mixing',
  'vaccines',
  'bodes',
  'well',
  'far

In [38]:
tokenised_trigrams

[['pfizer',
  'shot',
  'one',
  'finally',
  'syringe',
  'grateful',
  'covidvaccination',
  'pfizer',
  'thankyouscience'],
 ['sweet',
  'boy',
  'gabriel',
  'got',
  'first',
  'dose',
  'pfizer',
  'today',
  'champ'],
 ['est',
  'dose',
  'pfizer',
  'vaccine',
  'bucks',
  'county',
  'community',
  'college',
  'lower',
  'bucks',
  'campus'],
 ['got',
  'est',
  'coronavirus',
  'couid',
  'nineteen',
  'pfizer',
  'shot',
  'franciscan',
  'health',
  'hammond',
  'hammond'],
 ['pfizer', 'girl', 'yep'],
 ['wondering',
  'worth',
  'getting',
  'amp',
  'even',
  'though',
  'already',
  'got',
  'two',
  'pfizer',
  'shots',
  'figure',
  'double',
  'protection',
  'plus',
  'free',
  'hot',
  'dog'],
 ['second',
  'dose',
  'pfizer',
  'accomplished',
  'rest',
  'bit',
  'finishing',
  'packing',
  'cleaning',
  'donation',
  'runs'],
 ['anderson', 'got', 'tickets', 'pfizer'],
 ['think',
  'uk',
  'study',
  'looking',
  'mixing',
  'vaccines',
  'bodes',
  'well',
  'far

## Lemmatization

### Lemmatization with all postags

In [39]:
# TEST: lemmatisation of test_stopremoved
from nltk.stem import WordNetLemmatizer
lemmatizer=WordNetLemmatizer()
test_lemmatized = [lemmatizer.lemmatize(w)for w in test_stopremoved]
print(test_lemmatized)

['not', 'great', 'color', 'cruelty', 'free', 'use', 'elf', 'cosmetic', 'every', 'day', 'love']


In [40]:
#normal lemmatization of tokenised_stopremoved
from nltk.stem import WordNetLemmatizer
lemmatizer=WordNetLemmatizer()
tokenised_lemmatized_1 = [[lemmatizer.lemmatize(w) for w in each] for each in tokenised_bigrams]
tokenised_lemmatized_1

[['pfizer',
  'shot',
  'one',
  'finally',
  'syringe',
  'grateful',
  'covidvaccination',
  'pfizer',
  'thankyouscience'],
 ['sweet',
  'boy',
  'gabriel',
  'got',
  'first',
  'dose',
  'pfizer',
  'today',
  'champ'],
 ['est',
  'dose',
  'pfizer',
  'vaccine',
  'buck',
  'county',
  'community',
  'college',
  'lower',
  'buck',
  'campus'],
 ['got',
  'est',
  'coronavirus',
  'couid',
  'nineteen',
  'pfizer',
  'shot',
  'franciscan',
  'health',
  'hammond',
  'hammond'],
 ['pfizer', 'girl', 'yep'],
 ['wondering',
  'worth',
  'getting',
  'amp',
  'even',
  'though',
  'already',
  'got',
  'two',
  'pfizer',
  'shot',
  'figure',
  'double',
  'protection',
  'plus',
  'free',
  'hot',
  'dog'],
 ['second',
  'dose',
  'pfizer',
  'accomplished',
  'rest',
  'bit',
  'finishing',
  'packing',
  'cleaning',
  'donation',
  'run'],
 ['anderson', 'got', 'ticket', 'pfizer'],
 ['think',
  'uk',
  'study',
  'looking',
  'mixing',
  'vaccine',
  'bodes',
  'well',
  'far',
  '

### Lemmatisation with noun, adj, verb and adv

In [41]:
def lemmatization(texts, allowed_postags=['NOUN', 'ADJ', 'VERB', 'ADV']):
    """https://spacy.io/api/annotation"""
    texts_out = []
    for sent in texts:
        doc = nlp(" ".join(sent)) 
        texts_out.append([token.lemma_ for token in doc if token.pos_ in allowed_postags])
    return texts_out

In [42]:
import spacy 

# Initialize spacy 'en' model, keeping only tagger component (for efficiency)
nlp = spacy.load("en_core_web_sm", disable=['parser', 'ner'])

# Do lemmatization keeping only noun, adj, vb, adv
tokenised_lemmatized_2 = lemmatization(tokenised_bigrams, allowed_postags=['NOUN', 'ADJ', 'VERB', 'ADV'])
tokenised_lemmatized_2

[['pfizer',
  'shoot',
  'finally',
  'syringe',
  'grateful',
  'covidvaccination',
  'pfizer',
  'thankyouscience'],
 ['sweet', 'boy', 'get', 'first', 'dose', 'pfizer', 'today', 'champ'],
 ['est',
  'dose',
  'pfizer',
  'vaccine',
  'buck',
  'county',
  'community',
  'college',
  'low',
  'buck',
  'campus'],
 ['get',
  'est',
  'coronavirus',
  'couid',
  'pfizer',
  'shoot',
  'franciscan',
  'health',
  'hammond',
  'hammond'],
 ['pfizer', 'girl', 'yep'],
 ['wonder',
  'worth',
  'get',
  'amp',
  'even',
  'already',
  'get',
  'pfizer',
  'shot',
  'figure',
  'double',
  'protection',
  'free',
  'hot',
  'dog'],
 ['second',
  'dose',
  'pfizer',
  'accomplish',
  'rest',
  'bit',
  'finish',
  'packing',
  'cleaning',
  'donation',
  'run'],
 ['get', 'ticket', 'pfizer'],
 ['think',
  'study',
  'look',
  'mix',
  'vaccine',
  'bode',
  'well',
  'far',
  'suggest',
  'pfizer',
  'fact',
  'provide',
  'even',
  'well',
  'immunity',
  'fingers_crosse',
  'hold',
  'laugh'],

### Lemmatisation with nouns only

In [43]:
def lemmatization_noun(texts, allowed_postags=['NOUN']):
    """https://spacy.io/api/annotation"""
    texts_out = []
    for sent in texts:
        doc = nlp(" ".join(sent)) 
        texts_out.append([token.lemma_ for token in doc if token.pos_ in allowed_postags])
    return texts_out

In [44]:
import spacy 

# Initialize spacy 'en' model, keeping only tagger component (for efficiency)
nlp = spacy.load("en_core_web_sm", disable=['parser', 'ner'])

# Do lemmatization keeping only noun, adj, vb, adv
tokenised_lemmatized_3 = lemmatization_noun(tokenised_bigrams, allowed_postags=['NOUN'])
tokenised_lemmatized_3

[['pfizer', 'covidvaccination', 'pfizer', 'thankyouscience'],
 ['boy', 'dose', 'pfizer', 'today'],
 ['est',
  'dose',
  'pfizer',
  'vaccine',
  'buck',
  'county',
  'community',
  'college',
  'buck',
  'campus'],
 ['est', 'coronavirus', 'pfizer', 'health'],
 ['pfizer', 'girl'],
 ['amp', 'pfizer', 'shot', 'protection', 'dog'],
 ['dose', 'pfizer', 'rest', 'bit', 'packing', 'cleaning', 'donation'],
 ['ticket', 'pfizer'],
 ['study', 'vaccine', 'bode', 'pfizer', 'immunity'],
 ['pfizer', 'reading', 'label', 'product'],
 ['pfizer'],
 ['thing', 'pfizer', 'fakeness'],
 ['pfizer',
  'yesterday',
  'morning',
  'arm',
  'shot',
  'put',
  'case',
  'vaccine',
  'side',
  'effect'],
 [],
 ['baby', 'pfizer', 'girl', 'summer', 'syringe'],
 ['pfizer', 'pandemiclife', 'havee'],
 ['day', 'pfizer', 'biotech'],
 ['day', 'pfizer', 'tap', 'day'],
 ['antivaxxer',
  'indication',
  'indication',
  'blood',
  'transfusion',
  'vaccine',
  'pfizer',
  'blood'],
 ['pfizer', 'shot'],
 ['vaccinate'],
 ['county

### Gibberish Remover

In [45]:
#test
trial_nested=[['happy', 'time', 'ajsdnkfjak'],[],[],['dsnfkajka','yo','wassup']]

In [46]:
#test
len([])

if len([])== False:
    print('hi')

hi


In [47]:
#test
from gibberish_detector import detector
# load the gibberish detection model
Detector = detector.create_from_model('../../Gibberish-Detector-master/gibberish-detector.model')

##change variable tokenised_lemmatized_x

new_list = []

for alist in trial_nested:
    mini_list = []
    if len(alist):
        for word in alist:
            test = Detector.is_gibberish(word)
            if test == False:
                mini_list.append(word)
    new_list.append(mini_list)

In [48]:
#test
new_list

[['happy', 'time'], [], [], ['yo', 'wassup']]

In [49]:
#this is for tokenised_lemmatized_1
from gibberish_detector import detector
# load the gibberish detection model
Detector = detector.create_from_model('../../Gibberish-Detector-master/gibberish-detector.model')

##change variable tokenised_lemmatized_x
new_list = []

for alist in tokenised_lemmatized_1:
    mini_list = []
    if len(alist):
        for word in alist:
            test = Detector.is_gibberish(word)
            if test == False:
                mini_list.append(word)
    new_list.append(mini_list)
    
tokenised_lemmatized_1 = new_list

In [50]:
tokenised_lemmatized_1

[['pfizer',
  'shot',
  'one',
  'finally',
  'syringe',
  'grateful',
  'covidvaccination',
  'pfizer',
  'thankyouscience'],
 ['sweet',
  'boy',
  'gabriel',
  'got',
  'first',
  'dose',
  'pfizer',
  'today',
  'champ'],
 ['est',
  'dose',
  'pfizer',
  'vaccine',
  'buck',
  'county',
  'community',
  'college',
  'lower',
  'buck',
  'campus'],
 ['got',
  'est',
  'coronavirus',
  'couid',
  'nineteen',
  'pfizer',
  'shot',
  'franciscan',
  'health',
  'hammond',
  'hammond'],
 ['pfizer', 'girl', 'yep'],
 ['wondering',
  'worth',
  'getting',
  'amp',
  'even',
  'though',
  'already',
  'got',
  'two',
  'pfizer',
  'shot',
  'figure',
  'double',
  'protection',
  'plus',
  'free',
  'hot',
  'dog'],
 ['second',
  'dose',
  'pfizer',
  'accomplished',
  'rest',
  'bit',
  'finishing',
  'packing',
  'cleaning',
  'donation',
  'run'],
 ['anderson', 'got', 'ticket', 'pfizer'],
 ['think',
  'study',
  'looking',
  'mixing',
  'vaccine',
  'bodes',
  'well',
  'far',
  'suggesti

In [51]:
#this is for tokenised_lemmatized_2
from gibberish_detector import detector
# load the gibberish detection model
Detector = detector.create_from_model('../../Gibberish-Detector-master/gibberish-detector.model')

##change variable tokenised_lemmatized_x
new_list2 = []

for alist in tokenised_lemmatized_2:
    mini_list = []
    if len(alist):
        for word in alist:
            test = Detector.is_gibberish(word)
            if test == False:
                mini_list.append(word)
    new_list2.append(mini_list)
                
tokenised_lemmatized_2 = new_list2

In [52]:
tokenised_lemmatized_2

[['pfizer',
  'shoot',
  'finally',
  'syringe',
  'grateful',
  'covidvaccination',
  'pfizer',
  'thankyouscience'],
 ['sweet', 'boy', 'get', 'first', 'dose', 'pfizer', 'today', 'champ'],
 ['est',
  'dose',
  'pfizer',
  'vaccine',
  'buck',
  'county',
  'community',
  'college',
  'low',
  'buck',
  'campus'],
 ['get',
  'est',
  'coronavirus',
  'couid',
  'pfizer',
  'shoot',
  'franciscan',
  'health',
  'hammond',
  'hammond'],
 ['pfizer', 'girl', 'yep'],
 ['wonder',
  'worth',
  'get',
  'amp',
  'even',
  'already',
  'get',
  'pfizer',
  'shot',
  'figure',
  'double',
  'protection',
  'free',
  'hot',
  'dog'],
 ['second',
  'dose',
  'pfizer',
  'accomplish',
  'rest',
  'bit',
  'finish',
  'packing',
  'cleaning',
  'donation',
  'run'],
 ['get', 'ticket', 'pfizer'],
 ['think',
  'study',
  'look',
  'vaccine',
  'bode',
  'well',
  'far',
  'suggest',
  'pfizer',
  'fact',
  'provide',
  'even',
  'well',
  'immunity',
  'fingers_crosse',
  'hold',
  'laugh'],
 ['look'

In [53]:
#this is for tokenised_lemmatized_3
from gibberish_detector import detector
# load the gibberish detection model
Detector = detector.create_from_model('../../Gibberish-Detector-master/gibberish-detector.model')

##change variable tokenised_lemmatized_x
new_list3 = []

for alist in tokenised_lemmatized_3:
    mini_list = []
    if len(alist):
        for word in alist:
            test = Detector.is_gibberish(word)
            if test == False:
                mini_list.append(word)
    new_list3.append(mini_list)
                
tokenised_lemmatized_3 = new_list3

In [54]:
tokenised_lemmatized_3

[['pfizer', 'covidvaccination', 'pfizer', 'thankyouscience'],
 ['boy', 'dose', 'pfizer', 'today'],
 ['est',
  'dose',
  'pfizer',
  'vaccine',
  'buck',
  'county',
  'community',
  'college',
  'buck',
  'campus'],
 ['est', 'coronavirus', 'pfizer', 'health'],
 ['pfizer', 'girl'],
 ['amp', 'pfizer', 'shot', 'protection', 'dog'],
 ['dose', 'pfizer', 'rest', 'bit', 'packing', 'cleaning', 'donation'],
 ['ticket', 'pfizer'],
 ['study', 'vaccine', 'bode', 'pfizer', 'immunity'],
 ['pfizer', 'reading', 'label', 'product'],
 ['pfizer'],
 ['thing', 'pfizer', 'fakeness'],
 ['pfizer',
  'yesterday',
  'morning',
  'arm',
  'shot',
  'put',
  'case',
  'vaccine',
  'side',
  'effect'],
 [],
 ['baby', 'pfizer', 'girl', 'summer', 'syringe'],
 ['pfizer', 'pandemiclife', 'havee'],
 ['day', 'pfizer', 'biotech'],
 ['day', 'pfizer', 'tap', 'day'],
 ['antivaxxer',
  'indication',
  'indication',
  'blood',
  'transfusion',
  'vaccine',
  'pfizer',
  'blood'],
 ['pfizer', 'shot'],
 ['vaccinate'],
 ['county

## Creating column with Pre-processed words

In [55]:
df["words_processed_all"] = tokenised_lemmatized_1
df["words_processed_noun_adj_verb_adv"] = tokenised_lemmatized_2
df["words_processed_noun"] = tokenised_lemmatized_3

In [56]:
df.head()

Text  \
0  pfizer, shot, one, finally, syringe, so, very,...   
1  my, sweet, boy, gabriel, got, his, first, dose...   
2  est, dose, #, pfizer, vaccine, syringethumbs_u...   
3  i, just, got, my, est, coronavirus, couid, -, ...   
4                         i, i, i, pfizer, girl, yep   

                                    pos_tagged_words  \
0  [(pfizer, NN), (shot, NN), (one, CD), (finally...   
1  [(my, PRP$), (sweet, JJ), (boy, JJ), (gabriel,...   
2  [(est, JJS), (dose, JJ), (pfizer, NN), (vaccin...   
3  [(i, NN), (just, RB), (got, VBD), (my, PRP$), ...   
4  [(i, NN), (i, VBP), (i, VBP), (pfizer, VBP), (...   

                                 words_processed_all  \
0  [pfizer, shot, one, finally, syringe, grateful...   
1  [sweet, boy, gabriel, got, first, dose, pfizer...   
2  [est, dose, pfizer, vaccine, buck, county, com...   
3  [got, est, coronavirus, couid, nineteen, pfize...   
4                                [pfizer, girl, yep]   

                   words_processed_noun_adj_verb_adv  \
0  [pfizer, shoot, finally, syringe, grateful, co...   
1  [sweet, boy, get, first, dose, pfizer, today, ...   
2  [est, dose, pfizer, vaccine, buck, county, com...   
3  [get, est, coronavirus, couid, pfizer, shoot, ...   
4                                [pfizer, girl, yep]   

                                words_processed_noun  
0  [pfizer, covidvaccination, pfizer, thankyousci...  
1                         [boy, dose, pfizer, today]  
2  [est, dose, pfizer, vaccine, buck, county, com...  
3                 [est, coronavirus, pfizer, health]  
4                                     [pfizer, girl]

In [57]:
df.to_csv('usa-v2-preprocessed-97000-102000.csv')

## TFIDF

In [ ]:
df['words_processed_all']

In [ ]:
def listToString(s): 
    # initialize an empty string
    str1 = "" 
    # traverse in the string  
    for ele in s: 
        str1 += ele  
    # return string  
    return str1

In [ ]:
newlist = []

for each in df['words_processed_all']:
    new = each.strip("][").replace("'","").split(", ")
    newlist.append(new)

In [ ]:
newlist

In [ ]:
joined_list = []

for lis in newlist:
    new = " ".join(lis)
    joined_list.append(new)

In [ ]:
joined_list

In [ ]:
from sklearn.feature_extraction.text import TfidfTransformer
from sklearn.feature_extraction.text import CountVectorizer

In [ ]:
import pandas as pd
cv = CountVectorizer()
word_count_vector = cv.fit_transform(joined_list)
tf = pd.DataFrame(word_count_vector.toarray(), columns=cv.get_feature_names())
print(tf)

In [ ]:
tfidf_transformer = TfidfTransformer()
X = tfidf_transformer.fit_transform(word_count_vector)
idf = pd.DataFrame({'feature_name':cv.get_feature_names(), 'idf_weights':tfidf_transformer.idf_})
idf.sort_values('idf_weights', ascending=False, inplace=True)

In [ ]:
idf.to_csv('tfidf-descending.csv')

In [ ]:
tf_idf = pd.DataFrame(X.toarray(),columns=cv.get_feature_names())
tf_idf